In [4]:
import os
import rdkit
from rdkit import Chem
from tqdm import tqdm
import re
import py3Dmol
import subprocess

In [6]:
bridge_type = 'vp'
# res_path = '../../generation_results/' + bridge_type
res_path = '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/' + bridge_type

In [7]:
gen_files = os.listdir(res_path)
len(gen_files)

4339

In [8]:
raw_data_path = '../../data/cleaned_crossdocked_data/raw'

In [9]:
pdb_dict = {}
for directory in os.listdir(raw_data_path):
    dir_path = os.path.join(raw_data_path, directory)
    if os.path.isdir(dir_path):
        # Get the list of files in the directory
        files = os.listdir(dir_path)

        # Add the directory and its files to the dictionary
        pdb_dict[directory] = files

pdb_dict

{'METF_ECOLI_3_296_0': ['2fmn_B_rec_3fsu_mry_lig_tt_min_0.sdf',
  '3fsu_A_rec.pdb',
  '2fmn_B_rec.pdb',
  '3fsu_A_rec_3fsu_mry_lig_tt_min_0.sdf'],
 'CGGR_BACSU_86_340_0': ['3bxg_A_rec_3bxg_bg6_lig_tt_docked_2.sdf',
  '3bxf_A_rec_3bxh_f6p_lig_tt_min_0.sdf',
  '3bxe_A_rec_3bxg_bg6_lig_tt_min_0.sdf',
  '3bxe_A_rec_3bxh_f6p_lig_tt_min_0.sdf',
  '3bxh_A_rec_3bxh_f6p_lig_tt_min_0.sdf',
  '3bxh_A_rec.pdb',
  '2okg_B_rec.pdb',
  '3bxh_A_rec_3bxg_bg6_lig_tt_min_0.sdf',
  '3bxf_A_rec_3bxg_bg6_lig_tt_min_0.sdf',
  '3bxf_A_rec.pdb',
  '2okg_B_rec_3bxh_f6p_lig_tt_docked_3.sdf',
  '3bxe_A_rec_3bxg_bg6_lig_tt_docked_0.sdf',
  '2okg_B_rec_3bxg_bg6_lig_tt_docked_0.sdf',
  '3bxg_A_rec_3bxh_f6p_lig_tt_docked_2.sdf',
  '3bxg_A_rec_3bxh_f6p_lig_tt_min_0.sdf',
  '3bxh_A_rec_3bxh_f6p_lig_tt_docked_3.sdf',
  '3bxf_A_rec_3bxf_fbp_lig_tt_min_0.sdf',
  '2okg_B_rec_3bxh_f6p_lig_tt_min_0.sdf',
  '3bxe_A_rec.pdb',
  '3bxg_A_rec.pdb',
  '2okg_B_rec_3bxg_bg6_lig_tt_min_0.sdf',
  '3bxg_A_rec_3bxg_bg6_lig_tt_min_0.sdf'

In [10]:
pdb_rev_dict = {v:k for k, files in pdb_dict.items() for v in files}
pdb_rev_dict

{'2fmn_B_rec_3fsu_mry_lig_tt_min_0.sdf': 'METF_ECOLI_3_296_0',
 '3fsu_A_rec.pdb': 'METF_ECOLI_3_296_0',
 '2fmn_B_rec.pdb': 'METF_ECOLI_3_296_0',
 '3fsu_A_rec_3fsu_mry_lig_tt_min_0.sdf': 'METF_ECOLI_3_296_0',
 '3bxg_A_rec_3bxg_bg6_lig_tt_docked_2.sdf': 'CGGR_BACSU_86_340_0',
 '3bxf_A_rec_3bxh_f6p_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxe_A_rec_3bxg_bg6_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxe_A_rec_3bxh_f6p_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxh_A_rec_3bxh_f6p_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxh_A_rec.pdb': 'CGGR_BACSU_86_340_0',
 '2okg_B_rec.pdb': 'CGGR_BACSU_86_340_0',
 '3bxh_A_rec_3bxg_bg6_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxf_A_rec_3bxg_bg6_lig_tt_min_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxf_A_rec.pdb': 'CGGR_BACSU_86_340_0',
 '2okg_B_rec_3bxh_f6p_lig_tt_docked_3.sdf': 'CGGR_BACSU_86_340_0',
 '3bxe_A_rec_3bxg_bg6_lig_tt_docked_0.sdf': 'CGGR_BACSU_86_340_0',
 '2okg_B_rec_3bxg_bg6_lig_tt_docked_0.sdf': 'CGGR_BACSU_86_340_0',
 '3bxg_A_rec_3

In [11]:
len([file for file in gen_files if file in pdb_rev_dict.keys()])

4339

In [32]:
one = gen_files[765]
ligand_name = one.split('.')[0]

In [33]:
pattern = r"(\w+_[A-Z]_rec)"
match = re.search(pattern, one)
match.group(1)

'3fln_C_rec'

In [34]:
ligand_file = os.path.join(res_path, one)
ligand_file

'../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/vp/3fln_C_rec_3d7z_gk5_lig_tt_min_0.sdf'

In [35]:
pdb_folder = pdb_rev_dict[one]
pr_pdb = match.group(1)
protein_file = os.path.join(raw_data_path, pdb_folder, pr_pdb + '.pdb')
autobox_ligand_file = os.path.join(raw_data_path, pdb_folder, one)
print(protein_file, autobox_ligand_file)

../../data/cleaned_crossdocked_data/raw/MK14_HUMAN_1_360_0/3fln_C_rec.pdb ../../data/cleaned_crossdocked_data/raw/MK14_HUMAN_1_360_0/3fln_C_rec_3d7z_gk5_lig_tt_min_0.sdf


In [36]:
# log_path = '../../docking_res/logs/' + bridge_type
# out_path = '../../docking_res/output/' + bridge_type

log_path = '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/logs/' + bridge_type
out_path = '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/output/' + bridge_type
os.makedirs(log_path, exist_ok=True)
os.makedirs(out_path, exist_ok=True)

log_file = os.path.join(log_path, ligand_name + '.log')
out_file = os.path.join(out_path, ligand_name + '.sdf')
subprocess.run(['gnina', '-r', protein_file, '-l', ligand_file, '--autobox_ligand', autobox_ligand_file, '-o', out_file, '--exhaustiveness', '16', '--log', log_file, '-q'], stdout=subprocess.DEVNULL)

*** Open Babel Warning  in PerceiveBondOrders
  Failed to kekulize aromatic bonds in OBMol::PerceiveBondOrders



CompletedProcess(args=['gnina', '-r', '../../data/cleaned_crossdocked_data/raw/MK14_HUMAN_1_360_0/3fln_C_rec.pdb', '-l', '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/vp/3fln_C_rec_3d7z_gk5_lig_tt_min_0.sdf', '--autobox_ligand', '../../data/cleaned_crossdocked_data/raw/MK14_HUMAN_1_360_0/3fln_C_rec_3d7z_gk5_lig_tt_min_0.sdf', '-o', '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/output/vp/3fln_C_rec_3d7z_gk5_lig_tt_min_0.sdf', '--exhaustiveness', '16', '--log', '../../src/lightning_logs/vp_bridge_2024-05-11_10_25_47.519296/logs/vp/3fln_C_rec_3d7z_gk5_lig_tt_min_0.log', '-q'], returncode=0)

In [38]:
v = py3Dmol.view()
v.addModel(open(protein_file).read())
v.setStyle({'cartoon':{},'stick':{'radius':.1}})
v.addModel(open(autobox_ligand_file).read())
v.setStyle({'model':1},{'stick':{'colorscheme':'dimgrayCarbon','radius':.125}})
v.addModelsAsFrames(open(out_file).read())
v.setStyle({'model':2},{'stick':{'colorscheme':'greenCarbon','radius':.125}})
v.zoomTo({'model':1})
v.rotate(90)
v.animate({'interval':1000})

3Dmol.js failed to load for some reason. Please check your browser console for error messages.